In [1]:
import random
import json
import functools as fn
import numpy as np
import string
import hashlib

charset = string.ascii_lowercase+string.digits+',. '
charset_idmap = {e: i for i, e in enumerate(charset)}

ksz = 80

In [168]:
with open('./output.txt') as f:
    ctx = f.readline().strip()[4:]
    enc = bytes.fromhex(f.readline().strip()[6:])
ctx = [charset_idmap[c] for c in ctx]

with open('./ngrams.json') as f:
    ngrams = json.load(f)

In [169]:
def decrypt(ctx, key):
    N, ksz = len(charset), len(key)
    return ''.join(charset[(c-key[i % ksz]) % N] for i, c in enumerate(ctx))

def toPrintable(data):
    ul = ord('_')
    data = bytes(c if 32 <= c < 127 else ul for c in data)
    return data.decode('ascii')

@fn.lru_cache(10000)
def get_trigram(x):
    x = ''.join(x)
    y = ngrams.get(x)
    if y is not None:
        return y
    ys = []
    a, b = ngrams.get(x[:2]), ngrams.get(x[2:])
    if a is not None and b is not None:
        ys.append(a+b)
    a, b = ngrams.get(x[:1]), ngrams.get(x[1:])
    if a is not None and b is not None:
        ys.append(a+b)
    if len(ys):
        return max(ys)
    if any(c not in ngrams for c in x):
        return -25
    return sum(map(ngrams.get, x))

@fn.lru_cache(10000)
def fitness(a):
    plain = decrypt(ctx, a)
    tgs = zip(plain, plain[1:], plain[2:])
    score = sum(get_trigram(tg) for tg in tgs)
    return score

def initialize(size):
    population = []
    for i in range(size):
        key = tuple(random.randrange(len(charset)) for _ in range(ksz))
        population.append(key)
    return population

def crossover(a, b, prob):
    r = list(a)
    for i in range(len(r)):
        if random.random() < prob:
            r[i] = b[i]
    return tuple(r)

def mutate(a):
    r = list(a)
    i = random.randrange(len(a))
    r[i] = random.randrange(len(charset))
    return tuple(r)

In [170]:
INIT_P_SIZE = 5000
MAX_P_SIZE = 100
CROSSOVER_PROB = 0.5
ITER = 5000

def revolution(keys):
    np.random.shuffle(keys)
    for i in range(len(keys)//2):
        mutate_key = np.array(crossover(keys[i*2], keys[i*2+1], CROSSOVER_PROB))
        keys = np.concatenate((keys, [mutate_key]))
        
    np.random.shuffle(keys)
    for i in range(len(keys)//2):
        keys[i] = mutate(keys[i])

    scores = np.array([fitness(tuple(k)) for k in keys])
    
    candidates = np.flip(scores.argsort())[:MAX_P_SIZE]
    keys = keys[candidates]
    
    return keys, scores[candidates[0]]

In [171]:
keys = np.array(initialize(INIT_P_SIZE))
scores = np.array([fitness(tuple(k)) for k in keys])

candidates = np.flip(scores.argsort())[:MAX_P_SIZE]
keys = keys[candidates]

In [172]:
for i in range(ITER):
    keys, score = revolution(keys)
    print(i, score, decrypt(ctx, keys[0]))

0 -6454.344423590085 cpwzjl24nlp0swqgq aasi ce58a1eme0fhpqnfnhh,3o9hgmh, ft,eq196h 9etyy55hrd10hgss9zkywoooylon7lckqfhu pdhuhxzbyseee m20posw0zv 76iqh1nrppeq274 auf p fwb 6bsahlc10 pgvwhta8stwed4tw68bpjvvf4u,t8hno1diejtiohgd50csqqag azepz1l a10 ayc,la p0yn0lqsaakjsoo.,34yl,4rslsvafvgfd0b.tfgnza9h2hap2bykwin9h7g rs pqy5g4 yxr3b20c os8ngwvwtcpwzjlwu3suou4amqv2asi 8.3h s3ty4fc0scb3m4v819rwxfbolknf,q44fac0dzv1p v9 u.
1 -6385.431210841048 ifoexael9131rfcg7.sfooaynzp.58mfpark wzxy354 8.70e.c.pg,pxx71.odoixm sryfspuxiu0qoo62da5,3imb6cfytru nv36tvww8ef1h v.x 6eiqas5 evyouilnj13sautx.kwedik6w95pzhrlav9nbvippb9,fcnfwk7tuf1w1aorr .npq.s 522yy2.6lbje4,hc6vniyx au0f.8ibrsl ,eqvbqgdbgab,2dnrmh m9nds2rafb1h1muv9x9goo8gclquzgxtlhhexv4hckoiiputhl.dwmnaj7n 990vu1lhuifoexa.bm88ptnzm7uhfooarhx1,wutztamvblva3nq9m8ik.ccregw.9ms5z uz.juiwkvrqmg
2 -6383.070596370942 ifoexael9131rfcg7.sfooaynzp.58mfpark wzxy35408.70e.c.pg,pxx71.odoixm sryfspuxiu0qoo62da5,3imb6cfytru nv36tvww8ef1h v.x 6eiqag5 evyouilnj13sautx.k

In [173]:
ctx_inter = "gimli is a 384 bits na ftyction designed to achieve hi,  security with high performance across a bro. uk sie of platforms. it is curreelly in round 2 of the nist lightweight cryptoenvigne project, the submission coekisting of an authenticated encryption and a angistiraphic hash function. in th k paper, we focus on the gimli cipher, which na .nwos authenticated encryption nath associated data."
ctx_inter

'gimli is a 384 bits na ftyction designed to achieve hi,  security with high performance across a bro. uk sie of platforms. it is curreelly in round 2 of the nist lightweight cryptoenvigne project, the submission coekisting of an authenticated encryption and a angistiraphic hash function. in th k paper, we focus on the gimli cipher, which na .nwos authenticated encryption nath associated data.'

In [174]:
# ftyction => function (t (position: 24) -> u, y (position: 25) -> n)
ctx_inter.find('ftyction')

23

In [247]:
def decode_ctx(pos, key):
    return charset[(ctx[pos]-key[pos % len(key)]) % len(charset)]

def calc_offset(pos, key, to_char):
    target_id = charset_idmap[to_char]
    current_id = charset_idmap[charset[(ctx[pos]-key[pos % len(key)]) % len(charset)]]
    return target_id - current_id

def fix_key(pos, key, to_char):
    key[pos % len(key)] -= calc_offset(pos, key, to_char)
    return key

In [232]:
key = np.copy(keys[0])
decode_ctx(24, key)

't'

In [233]:
key[24] -= calc_offset(24, key, 'u')
key[25] -= calc_offset(25, key, 'n')

In [234]:
ctx_inter = decrypt(ctx, key)
ctx_inter

'gimli is a 384 bits na function designed to achieve hi,  security with high performance across a bro. ukahie of platforms. it is curreelly in round 2 of the nist lightweight cryptoenvihce project, the submission coekisting of an authenticated encryption and a angitiiraphic hash function. in th k paper, we focus on the gimli cipher, which na .olos authenticated encryption nath associated data.'

In [235]:
# hi,  => high
ctx_inter.find("hi, ")

52

In [236]:
key[54] -= calc_offset(54, key, 'g')
key[55] -= calc_offset(55, key, 'h')

In [237]:
ctx_inter = decrypt(ctx, key)
ctx_inter

'gimli is a 384 bits na function designed to achieve high security with high performance across a bro. ukahie of platforms. it is currently in round 2 of the nist lightweight cryptoenvihce project, the submission consisting of an authenticated encryption and a angitiiraphic hash function. in this paper, we focus on the gimli cipher, which na .olos authenticated encryption with associated data.'

## Round 2 of revolution

In [238]:
keys = np.array(initialize(INIT_P_SIZE))
keys = np.concatenate((keys, [key]))
scores = np.array([fitness(tuple(k)) for k in keys])

candidates = np.flip(scores.argsort())[:MAX_P_SIZE]
keys = keys[candidates]

for i in range(ITER):
    keys, score = revolution(keys)
    print(i, score, decrypt(ctx, keys[0]))

0 -3149.7553882895245 gimli is ap384 bits na function designed to achieve high security with high performance ac7oss a bro. ukahie of platforms. it is currently in round 2 of the nist lightweiwht cryptoenvihce project, the submission consisting of an authenticated encryptyon and a angitiiraphic hash function. in this paper, we focus on the gimli ciphur, which na .olos authenticated encryption with associated data.
1 -3149.7553882895245 gimli is ap384 bits na function designed to achieve high security with high performance ac7oss a bro. ukahie of platforms. it is currently in round 2 of the nist lightweiwht cryptoenvihce project, the submission consisting of an authenticated encryptyon and a angitiiraphic hash function. in this paper, we focus on the gimli ciphur, which na .olos authenticated encryption with associated data.
2 -3149.7553882895245 gimli is ap384 bits na function designed to achieve high security with high performance ac7oss a bro. ukahie of platforms. it is currently in 

In [239]:
ctx_inter = "gitli is a 384 bits maroutation designed to achieve high security with high perfortance across a bro,  tange of platforms. it is currently in round 2 of the nist sightweight cryptodnarhic project, the submission consisting of an authenticatedgencryption and a  nyrtographic hash function. in this paper, we focus on the gitli cipher, which marhorms authenticated encryption with associated data."
ctx_inter

'gitli is a 384 bits maroutation designed to achieve high security with high perfortance across a bro,  tange of platforms. it is currently in round 2 of the nist sightweight cryptodnarhic project, the submission consisting of an authenticatedgencryption and a  nyrtographic hash function. in this paper, we focus on the gitli cipher, which marhorms authenticated encryption with associated data.'

In [243]:
key = keys[0]

In [240]:
# maroutation -> permutation
ctx_inter.find('maroutation')

20

In [244]:
key = fix_key(20, key, 'p')
key = fix_key(21, key, 'e')
key = fix_key(23, key, 'm')

ctx_inter = decrypt(ctx, key)
ctx_inter

'gitli is a 384 bits permutation designed to achieve high security with high perfortance across a broad range of platforms. it is currently in round 2 of the nist sightweight cryptographic project, the submission consisting of an authenticatedgencryption and a cryptographic hash function. in this paper, we focus on the gitli cipher, which performs authenticated encryption with associated data.'

In [245]:
# sightweight -> lightweight
ctx_inter.find('sightweight')

162

In [248]:
key = fix_key(162, key, 'l')

ctx_inter = decrypt(ctx, key)
ctx_inter

'gimli is a 384 bits permutation designed to achieve high security with high performance across a broad range of platforms. it is currently in round 2 of the nist lightweight cryptographic project, the submission consisting of an authenticated encryption and a cryptographic hash function. in this paper, we focus on the gimli cipher, which performs authenticated encryption with associated data.'

# Decrypt enc

In [265]:
k = hashlib.sha512(''.join(charset[k % len(charset)] for k in key).encode('ascii')).digest()

In [268]:
for e_b, k_b in zip(enc, k):
    print(chr(e_b ^ k_b), end="")

FLAG{3c7166f852e3eaed71c81875e0c290562eff2c0}
                  